## Uczenie głębokie – przetwarzanie tekstu – laboratoria
# 3. RNN

In [54]:
# %pip install torch
# %pip install ipywidgets
# %pip install pandas
# %pip install transformers

In [55]:
!jupyter nbextension enable --py widgetsnbextension
import torch
from ipywidgets import FloatProgress
import pandas as pd

usage: jupyter [-h] [--version] [--config-dir] [--data-dir] [--runtime-dir]
               [--paths] [--json] [--debug]
               [subcommand]

Jupyter: Interactive Computing

positional arguments:
  subcommand     the subcommand to launch

options:
  -h, --help     show this help message and exit
  --version      show the versions of core jupyter packages and exit
  --config-dir   show Jupyter config dir
  --data-dir     show Jupyter data dir
  --runtime-dir  show Jupyter runtime dir
  --paths        show all Jupyter paths. Add --json for machine-readable
                 format.
  --json         output paths as machine-readable json
  --debug        output debug information about paths

Available subcommands: console dejavu events execute kernel kernelspec lab
labextension labhub migrate nbconvert notebook qtconsole run server
troubleshoot trust

Jupyter command `jupyter-nbextension` not found.


In [56]:
from transformers import AutoModelForTokenClassification, AutoTokenizer, pipeline

model = AutoModelForTokenClassification.from_pretrained("dslim/bert-base-NER")
tokenizer = AutoTokenizer.from_pretrained("dslim/bert-base-NER")

nlp = pipeline("ner", model=model, tokenizer=tokenizer)

Some weights of the model checkpoint at dslim/bert-base-NER were not used when initializing BertForTokenClassification: ['bert.pooler.dense.bias', 'bert.pooler.dense.weight']
- This IS expected if you are initializing BertForTokenClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForTokenClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [57]:
# odczytaj dane treningowe
train = pd.read_csv('train/train.tsv', sep='\t', names=['y', 'x'], header=None)

print("wczytano dane treningowe")
print(train["y"][0], train["x"][0])

print(len(train["y"][0].split(" ")))
print(len(train["x"][0].split(" ")))

print(train["x"][0])

wczytano dane treningowe
B-ORG O B-MISC O O O B-MISC O O O B-PER I-PER O B-LOC O O O B-ORG I-ORG O O O O O O B-MISC O O O O O B-MISC O O O O O O O O O O O O O O O B-LOC O O O O B-ORG I-ORG O O O B-PER I-PER O O O O O O O O O O O B-LOC O O O O O O O O O O O O O O O O O O O O O O O O O O O O B-ORG O O O B-PER I-PER I-PER I-PER O O O O O O O O O O O O O O O O O O O O O O O O O O O O B-ORG I-ORG O O O O O O O O O B-ORG O O B-PER I-PER O O O O O O O O O O O O O O O O O O O O O O O O O O O O O B-PER O B-MISC O O O O B-LOC O B-LOC O O O O O O O B-MISC I-MISC I-MISC O B-MISC O O O O O O O O B-PER O O O O O O O B-ORG O O O O O O O O O O O O O O O O O O O O O O O O O O O O B-MISC O O B-PER I-PER I-PER O O O B-PER O O B-ORG O O O O O O O O O O O O O O O O O O B-LOC O B-LOC O B-PER O O O O O B-ORG O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O B-MISC O O O O O O O O O O O O O O O O B-MISC O O O O O O O O O O O O O O O O O O O B-MISC O O O O O O B-MISC O O O O O B-LOC

In [58]:
# odczytaj dane testowe dev-0
test_dev0 = pd.read_csv('dev-0/in.tsv', sep='\t', names=['x'], header=None)

print("wczytano dane testowe dev-0")
print(test_dev0["x"][0])

wczytano dane testowe dev-0
CRICKET - LEICESTERSHIRE TAKE OVER AT TOP AFTER INNINGS VICTORY . </S> LONDON 1996-08-30 </S> West Indian all-rounder Phil Simmons took four for 38 on Friday as Leicestershire beat Somerset by an innings and 39 runs in two days to take over at the head of the county championship . </S> Their stay on top , though , may be short-lived as title rivals Essex , Derbyshire and Surrey all closed in on victory while Kent made up for lost time in their rain-affected match against Nottinghamshire . </S> After bowling Somerset out for 83 on the opening morning at Grace Road , Leicestershire extended their first innings by 94 runs before being bowled out for 296 with England discard Andy Caddick taking three for 83 . </S> Trailing by 213 , Somerset got a solid start to their second innings before Simmons stepped in to bundle them out for 174 . </S> Essex , however , look certain to regain their top spot after Nasser Hussain and Peter Such gave them a firm grip on their 

In [59]:
# odczytaj dane testowe A
test_A = pd.read_csv('test-A/in.tsv', sep='\t', names=['x'], header=None)

print("wczytano dane testowe A")
print(test_A["x"][0])

wczytano dane testowe A
SOCCER - JAPAN GET LUCKY WIN , CHINA IN SURPRISE DEFEAT . </S> Nadim Ladki </S> AL-AIN , United Arab Emirates 1996-12-06 </S> Japan began the defence of their Asian Cup title with a lucky 2-1 win against Syria in a Group C championship match on Friday . </S> But China saw their luck desert them in the second match of the group , crashing to a surprise 2-0 defeat to newcomers Uzbekistan . </S> China controlled most of the match and saw several chances missed until the 78th minute when Uzbek striker Igor Shkvyrin took advantage of a misdirected defensive header to lob the ball over the advancing Chinese keeper and into an empty net . </S> Oleg Shatskiku made sure of the win in injury time , hitting an unstoppable left foot shot from just outside the area . </S> The former Soviet republic was playing in an Asian Cup finals tie for the first time . </S> Despite winning the Asian Games title two years ago , Uzbekistan are in the finals as outsiders . </S> Two goals f

In [60]:
# odczytaj etykiety dev-0
labels_dev0 = pd.read_csv('dev-0/expected.tsv', sep='\t', names=['y'], header=None)

print(len(labels_dev0["y"][0].split(" ")))
print(labels_dev0["y"][0])

456
O O B-ORG O O O O O O O O O B-LOC O O B-MISC I-MISC O B-PER I-PER O O O O O O O B-ORG O B-ORG O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O B-ORG O B-ORG O B-ORG O O O O O O B-ORG O O O O O O O O O O B-ORG O O O O B-ORG O O O O O O O O B-LOC I-LOC O B-ORG O O O O O O O O O O O O O O B-LOC O B-PER I-PER O O O O O O O O O O B-ORG O O O O O O O O O B-PER O O O O O O O O O O B-ORG O O O O O O O O O O O B-PER I-PER O B-PER I-PER O O O O O O O O O B-ORG O B-LOC O O B-PER O O O O B-LOC O O O O O O O O O O O O O O O O B-ORG O O O O O O O O O O O O O O O B-ORG O O O O O O O O O B-PER O O O O O O O O O O O O O O O O O O O O O O O O O O O O B-LOC O B-ORG O B-PER I-PER O O O O O B-LOC O O O O O O O O O O O O O O O O O O O O O O O O O B-ORG O O O O O O O B-LOC O B-PER I-PER O O O O B-ORG O O O O O O O O O O O O B-ORG O O O O O O O O O O O O O B-ORG O O O O O O O O O O O O O O O O O O O O B-MISC B-PER I-PER O O O O O B-PER I-PER O O O O B-PER I-PER O O O O B-ORG O O O O O O

In [61]:
# przewidywania dev0
print(test_dev0["x"][0])
print(labels_dev0["y"][0])

predicted_labels_dev0 = []
for tekst in test_dev0["x"]:
    predicted_labels_dev0.append(nlp(tekst))

print(predicted_labels_dev0[0])

CRICKET - LEICESTERSHIRE TAKE OVER AT TOP AFTER INNINGS VICTORY . </S> LONDON 1996-08-30 </S> West Indian all-rounder Phil Simmons took four for 38 on Friday as Leicestershire beat Somerset by an innings and 39 runs in two days to take over at the head of the county championship . </S> Their stay on top , though , may be short-lived as title rivals Essex , Derbyshire and Surrey all closed in on victory while Kent made up for lost time in their rain-affected match against Nottinghamshire . </S> After bowling Somerset out for 83 on the opening morning at Grace Road , Leicestershire extended their first innings by 94 runs before being bowled out for 296 with England discard Andy Caddick taking three for 83 . </S> Trailing by 213 , Somerset got a solid start to their second innings before Simmons stepped in to bundle them out for 174 . </S> Essex , however , look certain to regain their top spot after Nasser Hussain and Peter Such gave them a firm grip on their match against Yorkshire at H

In [62]:
# zakladamy ze teksty nie zaczynaj ani nie koncza sie na spacji, nie ma wielokrotnych spacji
zakresy_slow_tekstow = []
for tekst in test_dev0["x"]:
    zakresy_slow = []
    poczatek = 0
    koniec = len(tekst)-1
    for numer_zakresu in range(len(tekst)):
        znak = tekst[numer_zakresu]
        if znak == " ":
            koniec = numer_zakresu-1
            zakres = (poczatek, koniec)
            zakresy_slow.append(zakres)
            poczatek = numer_zakresu+1
            koniec = len(tekst)-1
    zakres = (poczatek, koniec)
    zakresy_slow.append(zakres)
    zakresy_slow_tekstow.append(zakresy_slow)

print(test_dev0["x"][0])
print(zakresy_slow_tekstow[0])

print(len(labels_dev0["y"][0].split(" ")))
print(len(zakresy_slow_tekstow[0]))

CRICKET - LEICESTERSHIRE TAKE OVER AT TOP AFTER INNINGS VICTORY . </S> LONDON 1996-08-30 </S> West Indian all-rounder Phil Simmons took four for 38 on Friday as Leicestershire beat Somerset by an innings and 39 runs in two days to take over at the head of the county championship . </S> Their stay on top , though , may be short-lived as title rivals Essex , Derbyshire and Surrey all closed in on victory while Kent made up for lost time in their rain-affected match against Nottinghamshire . </S> After bowling Somerset out for 83 on the opening morning at Grace Road , Leicestershire extended their first innings by 94 runs before being bowled out for 296 with England discard Andy Caddick taking three for 83 . </S> Trailing by 213 , Somerset got a solid start to their second innings before Simmons stepped in to bundle them out for 174 . </S> Essex , however , look certain to regain their top spot after Nasser Hussain and Peter Such gave them a firm grip on their match against Yorkshire at H

In [63]:
poprawione_predicted_labels_dev0 = []
for linijka in range(len(test_dev0["x"])):
    zakresy_slow = zakresy_slow_tekstow[linijka]
    przewidywania = predicted_labels_dev0[linijka]
    etykiety = ["O" for _ in zakresy_slow]
    for numer_zakresu in range(len(zakresy_slow)):
        zakres = zakresy_slow[numer_zakresu]
        for p in przewidywania:
            start = p["start"]
            if start>=zakres[0] and start<=zakres[1]:
                tag = p["entity"]
                if etykiety[numer_zakresu] == "O":
                    etykiety[numer_zakresu] = tag
    poprawione_predicted_labels_dev0.append(" ".join(etykiety).strip())

In [ ]:
print(labels_dev0["y"][0])
print(poprawione_predicted_labels_dev0[0])

print(len(labels_dev0["y"][0].split(" ")))
print(len(poprawione_predicted_labels_dev0[0].split(" ")))

O O B-ORG O O O O O O O O O B-LOC O O B-MISC I-MISC O B-PER I-PER O O O O O O O B-ORG O B-ORG O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O B-ORG O B-ORG O B-ORG O O O O O O B-ORG O O O O O O O O O O B-ORG O O O O B-ORG O O O O O O O O B-LOC I-LOC O B-ORG O O O O O O O O O O O O O O B-LOC O B-PER I-PER O O O O O O O O O O B-ORG O O O O O O O O O B-PER O O O O O O O O O O B-ORG O O O O O O O O O O O B-PER I-PER O B-PER I-PER O O O O O O O O O B-ORG O B-LOC O O B-PER O O O O B-LOC O O O O O O O O O O O O O O O O B-ORG O O O O O O O O O O O O O O O B-ORG O O O O O O O O O B-PER O O O O O O O O O O O O O O O O O O O O O O O O O O O O B-LOC O B-ORG O B-PER I-PER O O O O O B-LOC O O O O O O O O O O O O O O O O O O O O O O O O O B-ORG O O O O O O O B-LOC O B-PER I-PER O O O O B-ORG O O O O O O O O O O O O B-ORG O O O O O O O O O O O O O B-ORG O O O O O O O O O O O O O O O O O O O O B-MISC B-PER I-PER O O O O O B-PER I-PER O O O O B-PER I-PER O O O O B-ORG O O O O O O O O

In [65]:
with open("dev-0/out.tsv", "w", encoding="utf-8") as uwu:
    for linijka in poprawione_predicted_labels_dev0:
        uwu.write(linijka)
        uwu.write(str("\n"))

# test A

In [67]:
# przewidywania testA
print(test_A["x"][0])

predicted_labels_A = []
for tekst in test_A["x"]:
    predicted_labels_A.append(nlp(tekst))

print(predicted_labels_A[0])

SOCCER - JAPAN GET LUCKY WIN , CHINA IN SURPRISE DEFEAT . </S> Nadim Ladki </S> AL-AIN , United Arab Emirates 1996-12-06 </S> Japan began the defence of their Asian Cup title with a lucky 2-1 win against Syria in a Group C championship match on Friday . </S> But China saw their luck desert them in the second match of the group , crashing to a surprise 2-0 defeat to newcomers Uzbekistan . </S> China controlled most of the match and saw several chances missed until the 78th minute when Uzbek striker Igor Shkvyrin took advantage of a misdirected defensive header to lob the ball over the advancing Chinese keeper and into an empty net . </S> Oleg Shatskiku made sure of the win in injury time , hitting an unstoppable left foot shot from just outside the area . </S> The former Soviet republic was playing in an Asian Cup finals tie for the first time . </S> Despite winning the Asian Games title two years ago , Uzbekistan are in the finals as outsiders . </S> Two goals from defensive errors in 

In [68]:
# zakladamy ze teksty nie zaczynaj ani nie koncza sie na spacji, nie ma wielokrotnych spacji
zakresy_slow_tekstow = []
for tekst in test_A["x"]:
    zakresy_slow = []
    poczatek = 0
    koniec = len(tekst)-1
    for numer_zakresu in range(len(tekst)):
        znak = tekst[numer_zakresu]
        if znak == " ":
            koniec = numer_zakresu-1
            zakres = (poczatek, koniec)
            zakresy_slow.append(zakres)
            poczatek = numer_zakresu+1
            koniec = len(tekst)-1
    zakres = (poczatek, koniec)
    zakresy_slow.append(zakres)
    zakresy_slow_tekstow.append(zakresy_slow)

print(test_A["x"][0])
print(zakresy_slow_tekstow[0])

print(len(test_A["x"][0].split(" ")))
print(len(zakresy_slow_tekstow[0]))

SOCCER - JAPAN GET LUCKY WIN , CHINA IN SURPRISE DEFEAT . </S> Nadim Ladki </S> AL-AIN , United Arab Emirates 1996-12-06 </S> Japan began the defence of their Asian Cup title with a lucky 2-1 win against Syria in a Group C championship match on Friday . </S> But China saw their luck desert them in the second match of the group , crashing to a surprise 2-0 defeat to newcomers Uzbekistan . </S> China controlled most of the match and saw several chances missed until the 78th minute when Uzbek striker Igor Shkvyrin took advantage of a misdirected defensive header to lob the ball over the advancing Chinese keeper and into an empty net . </S> Oleg Shatskiku made sure of the win in injury time , hitting an unstoppable left foot shot from just outside the area . </S> The former Soviet republic was playing in an Asian Cup finals tie for the first time . </S> Despite winning the Asian Games title two years ago , Uzbekistan are in the finals as outsiders . </S> Two goals from defensive errors in 

In [69]:
poprawione_predicted_labels_A = []
for linijka in range(len(test_A["x"])):
    zakresy_slow = zakresy_slow_tekstow[linijka]
    przewidywania = predicted_labels_A[linijka]
    etykiety = ["O" for _ in zakresy_slow]
    for numer_zakresu in range(len(zakresy_slow)):
        zakres = zakresy_slow[numer_zakresu]
        for p in przewidywania:
            start = p["start"]
            if start>=zakres[0] and start<=zakres[1]:
                tag = p["entity"]
                if etykiety[numer_zakresu] == "O":
                    etykiety[numer_zakresu] = tag
    poprawione_predicted_labels_A.append(" ".join(etykiety).strip())

In [70]:
print(test_A["x"][0])
print(poprawione_predicted_labels_A[0])

print(len(test_A["x"][0].split(" ")))
print(len(poprawione_predicted_labels_A[0].split(" ")))

SOCCER - JAPAN GET LUCKY WIN , CHINA IN SURPRISE DEFEAT . </S> Nadim Ladki </S> AL-AIN , United Arab Emirates 1996-12-06 </S> Japan began the defence of their Asian Cup title with a lucky 2-1 win against Syria in a Group C championship match on Friday . </S> But China saw their luck desert them in the second match of the group , crashing to a surprise 2-0 defeat to newcomers Uzbekistan . </S> China controlled most of the match and saw several chances missed until the 78th minute when Uzbek striker Igor Shkvyrin took advantage of a misdirected defensive header to lob the ball over the advancing Chinese keeper and into an empty net . </S> Oleg Shatskiku made sure of the win in injury time , hitting an unstoppable left foot shot from just outside the area . </S> The former Soviet republic was playing in an Asian Cup finals tie for the first time . </S> Despite winning the Asian Games title two years ago , Uzbekistan are in the finals as outsiders . </S> Two goals from defensive errors in 

In [71]:
with open("test-A/out.tsv", "w", encoding="utf-8") as uwu:
    for linijka in poprawione_predicted_labels_A:
        uwu.write(linijka)
        uwu.write(str("\n"))